## (1) 모델 import

In [1]:
base_dir = r'C:\Users\Yang\Desktop\project'

In [2]:
from keras.models import load_model

model = load_model(base_dir+'\model\model.h5')

Using TensorFlow backend.






Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


In [2]:
from gensim.models import Word2Vec
import csv
import re

model1 = Word2Vec.load(base_dir + '\word_model\Word2vec.model')
word_vectors = model1.wv
vocabs = word_vectors.vocab.keys()
word_vectors_list = [word_vectors[v] for v in vocabs]

# 품사 태깅(주어진 텍스트를 형태소 단위로 나누고 나눠진 형태소를 해당하는 품사와 함께 리스트화)
# stemming(단어들을 원형으로 포현), normalization(표현 방법이 다른 단어들을 통합시켜 같은 단어로 만듬)
import json
import os
from konlpy.tag import Okt

okt = Okt()

def tokenize(doc): # 형태소 분석기인 Okt를 이용해서 품사를 태깅시킴
    # norm은 정규화, stem은 근어로 표시하기를 나타냄
    return ['/'.join(t) for t in okt.pos(doc, norm=True, stem=True)]

os.chdir(base_dir) # 경로 설정

C:\Users\0000\Anaconda3\lib\site-packages\gensim\utils.py:1197: UserWarning: detected Windows; aliasing chunkize to chunkize_serial
  warnings.warn("detected Windows; aliasing chunkize to chunkize_serial")
C:\Users\0000\Anaconda3\lib\site-packages\smart_open\smart_open_lib.py:398: UserWarning: This function is deprecated, use smart_open.open instead. See the migration notes for details: https://github.com/RaRe-Technologies/smart_open/blob/master/README.rst#migrating-to-the-new-open-function
  'See the migration notes for details: %s' % _MIGRATION_NOTES_URL
C:\Users\0000\Anaconda3\lib\site-packages\jpype\_core.py:210: UserWarning: 
-------------------------------------------------------------------------------
Deprecated: convertStrings was not specified when starting the JVM. The default
behavior in JPype will be False starting in JPype 0.8. The recommended setting
for new code is convertStrings=False.  The legacy value of True was assumed for
this session. If you are a user of an appl

## (2) Test 데이터 import

In [3]:
# csv파일 불러옴
import csv
import re

# test할 기사를 articles에 저장
# articles는 문장이 아니고 기사 별로 저장
articles = [] 

# ytn 기사 원본을 가지고 test 진행
f = open(base_dir + '\data\ytn_article.csv', 'r', encoding='utf-8') 
rdr = csv.reader(f)
for line in rdr:
    articles.append(line)
f.close() 

In [4]:
# 빈 text 제거 & 특수문자 제거
articles = [i for i in articles if len(i[0])>=10]
articles2 = []
for i in range(len(articles)):
    if(articles[i] is not ' '):
        newarticle = re.sub('[-=+,#/\?:^$@*\"~&%!<>()◇"]', '', articles[i][0])
        articles2.append([newarticle])

## (3-1) Test 데이터를 Neural network 모델에 적용

In [5]:
from sentence_utility import zero_padding, circular_padding, reverse_padding

In [11]:
# -*- coding:utf-8 -*-
import csv    
import numpy as np

# 테스트 결과를 predict_output.csv 파일에 저장
f = open(base_dir + '\prediction\predict_output3.csv', 'w', encoding='utf_8_sig', newline='')
wr = csv.writer(f)
all_sents = []
all_vec_sents = []

for article in articles2:
    temp = re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', article[0]) # 기사를 문장 별로 나눔.
    sents_raw = [] # 문장으로 나눴을 때 문장들
    
    for i in temp:
        # 위에서 쪼갰을 때, 마침표와 다음 문장이 붙어있는 경우에는 한 문장으로 인식하는 문제 발생. 
        # 예를 들어 '안녕하세요.반가워요.'의 경우 한 문장으로 인식.
        # 아래 라인을 통해 위와 같은 경우도 나눠줌.
        sents_raw += (re.split('[\.]',i)) 
        
    sents_raw_over10 = [i for i in sents_raw if len(i)>=10] # 단일 문장들 중 10단어 이상의 문장만 선택.
    sents = sents_raw_over10

    token_sents = [] # word_vectors의 key가 '단어/품사'의 형식으로 되어 있기 때문에, 같은 형식으로 만들기 위해 각 문장별로 tokenize를 적용함.
    for sent in sents:
        token_sents.append(tokenize(sent))
        
    vec_sents = [] # word embedding 결과
    sents_index = 0
    for token_sent in token_sents:
        temp_sent = []
        for token_word in token_sent:
            # '만조/Noun' 같은 단어가 word_vectors 안에 없는 경우가 있어서
            # 이런 경우에는 단어를 추가하지 않고, 지나가도록 만듦.
            try:
                temp_sent.append(word_vectors.get_vector(token_word))
            except KeyError:# key가 존재하지 않을 때
                pass # 그냥 지나감 
        if len(temp_sent) != 0:
            all_sents.append(sents[sents_index])
            vec_sents.append(temp_sent)
        sents_index += 1
    # 벡터화 완료
    all_vec_sents = all_vec_sents + vec_sents
    sentences = np.asarray(vec_sents) # 벡터화 완료된 문장들
    
    ##########################################################################################
    # <Padding>
    # 문장마다 단어의 갯수가 다른 문제가 있음.
    # 이를 해결하기 위해, 문장 안의 단어 갯수를 50으로 맞춰줌.
    # 단어 갯수가 50이하 이면 아래의 세가지 padding 중 하나를 선택해서 길이를 50으로 맞춰줌.
    new_sentences = zero_padding(sentences)
    # new_sentences = circular_padding(sentences)
    # new_sentences = reverse_padding(sentences)    
    ##########################################################################################
    
    index = [] # 하나의 기사를 model을 통해서 예측한 후, 피해 문장이라고 예측된 문장의 기사 안에서의 위치(index)를 저장.
    result = model.predict(new_sentences)
    for i in range(len(new_sentences)):
        if(result[i][0] < 0.5): 
            index.append(i)
            
    damage_sents = [] # index를 통해서 피해 문장을 저장.
    for i in index:
        damage_sents.append(sents[i])

    wr.writerow([article[0], damage_sents])
    
f.close()

# (3-2) Test 데이터를 Machine learning 모델에 적용

In [6]:
import pickle

xgb_model = pickle.load(open("xgb.dat", "rb"))

[11:20:28] WARNING: src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.


In [12]:
# (3-1)을 실행해야지 all_vec_sents가 생성됨
all_sentences = np.asarray(all_vec_sents)
mean_sents = []
for i in range(len(all_sentences)):
    #mean_sents = mean_sents + np.mean(sentences[i], axis=0)
    mean_sents.append(np.mean(all_sentences[i], axis=0))

In [13]:
pred_xgb = xgb_model.predict(mean_sents)

In [14]:
pred_xgb_sents = np.array(all_sents)[pred_xgb > 0.5]

In [24]:
f = open(base_dir + '\prediction\predict_output_xgb.csv', 'w', encoding='utf_8_sig', newline='')
wr = csv.writer(f)
pred_xgb_tf = pred_xgb > 0.5
for i in range(len(all_sents)):
    wr.writerow([all_sents[i], pred_xgb_tf[i]])
f.close()

In [22]:
pred_xgb > 0.5

array([False, False, False, ..., False, False, False])

# (3-3) Test 데이터를 앙상블 모델에 적용

In [3]:
from keras.models import load_model

model_list = []
total_num_model = 50
for i in range(total_num_model):
    model = load_model(base_dir+'\model\lstm_zeroPadding'+str(i)+'.h5')
    model_list.append(model)    

In [7]:
import csv    
import numpy as np
from sentence_utility import zero_padding, circular_padding, reverse_padding

f = open(base_dir + '\prediction\predict_output_ensemble.csv', 'w', encoding='utf_8_sig', newline='')
wr = csv.writer(f)
all_sents = []
all_vec_sents = []

k = 0
for article in articles2:
    print(k)
    k = k + 1
    temp = re.split(r'(?<!\w\.\w.)(?<![A-Z][a-z]\.)(?<=\.|\?)\s', article[0]) # 기사를 문장 별로 나눔.
    sents_raw = [] # 문장으로 나눴을 때 문장들
    
    for i in temp:
        # 위에서 쪼갰을 때, 마침표와 다음 문장이 붙어있는 경우에는 한 문장으로 인식하는 문제 발생. 
        # 예를 들어 '안녕하세요.반가워요.'의 경우 한 문장으로 인식.
        # 아래 라인을 통해 위와 같은 경우도 나눠줌.
        sents_raw += (re.split('[\.]',i)) 
        
    sents_raw_over10 = [i for i in sents_raw if len(i)>=10] # 단일 문장들 중 10단어 이상의 문장만 선택.
    sents = sents_raw_over10

    token_sents = [] # word_vectors의 key가 '단어/품사'의 형식으로 되어 있기 때문에, 같은 형식으로 만들기 위해 각 문장별로 tokenize를 적용함.
    for sent in sents:
        token_sents.append(tokenize(sent))
        
    vec_sents = [] # word embedding 결과
    sents_index = 0
    for token_sent in token_sents:
        temp_sent = []
        for token_word in token_sent:
            # '만조/Noun' 같은 단어가 word_vectors 안에 없는 경우가 있어서
            # 이런 경우에는 단어를 추가하지 않고, 지나가도록 만듦.
            try:
                temp_sent.append(word_vectors.get_vector(token_word))
            except KeyError:# key가 존재하지 않을 때
                pass # 그냥 지나감 
        if len(temp_sent) != 0:
            all_sents.append(sents[sents_index])
            vec_sents.append(temp_sent)
        sents_index += 1
    # 벡터화 완료
    all_vec_sents = all_vec_sents + vec_sents
    sentences = np.asarray(vec_sents) # 벡터화 완료된 문장들
    
    ##########################################################################################
    # <Padding>
    # 문장마다 단어의 갯수가 다른 문제가 있음.
    # 이를 해결하기 위해, 문장 안의 단어 갯수를 50으로 맞춰줌.
    # 단어 갯수가 50이하 이면 아래의 세가지 padding 중 하나를 선택해서 길이를 50으로 맞춰줌.
    new_sentences = zero_padding(sentences)
    # new_sentences = circular_padding(sentences)
    # new_sentences = reverse_padding(sentences)    
    ##########################################################################################
    
    index = [] # 하나의 기사를 model을 통해서 예측한 후, 피해 문장이라고 예측된 문장의 기사 안에서의 위치(index)를 저장.
    result = np.zeros((new_sentences.shape[0], 2))
    for i in range(total_num_model):
        print('Model: '+str(i))
        model = model_list[i]
        result += model.predict(new_sentences)
        
    result = result/total_num_model
    
    for i in range(len(new_sentences)):
        if(result[i][0] < 0.5): 
            index.append(i)
            
    damage_sents = [] # index를 통해서 피해 문장을 저장.
    for i in index:
        damage_sents.append(sents[i])
        
#   final_sents = [] # 피해관련 단어가 포함된 문장들
    
#     for sent in damage_sents:
#         if '피해' in str(sent):
#             final_sents.append(sent)
    
#     ffinal_sents = []
    
#     for sent in final_sents:
#         for damage in words_damage:
#             if damage in str(sent):
#                 ffinal_sents.append(sent)
    wr.writerow([article[0], damage_sents])
    
f.close()

0
Model: 0
Model: 1
Model: 2
Model: 3
Model: 4
Model: 5
Model: 6
Model: 7
Model: 8
Model: 9
Model: 10
Model: 11
Model: 12
Model: 13
Model: 14
Model: 15
Model: 16
Model: 17
Model: 18
Model: 19
Model: 20
Model: 21
Model: 22
Model: 23
Model: 24
Model: 25
Model: 26
Model: 27
Model: 28
Model: 29
Model: 30
Model: 31
Model: 32
Model: 33
Model: 34
Model: 35
Model: 36
Model: 37
Model: 38
Model: 39
Model: 40
Model: 41
Model: 42
Model: 43
Model: 44
Model: 45
Model: 46
Model: 47
Model: 48
Model: 49
1
Model: 0
Model: 1
Model: 2
Model: 3
Model: 4
Model: 5
Model: 6
Model: 7
Model: 8
Model: 9
Model: 10
Model: 11
Model: 12
Model: 13
Model: 14
Model: 15
Model: 16
Model: 17
Model: 18
Model: 19
Model: 20
Model: 21
Model: 22
Model: 23
Model: 24
Model: 25
Model: 26
Model: 27
Model: 28
Model: 29
Model: 30
Model: 31
Model: 32
Model: 33
Model: 34
Model: 35
Model: 36
Model: 37
Model: 38
Model: 39
Model: 40
Model: 41
Model: 42
Model: 43
Model: 44
Model: 45
Model: 46
Model: 47
Model: 48
Model: 49
2
Model: 0
Model